# Predicting Flight Delays: Phase I
##### Team: House of Spark
##### Phase I Lead: Neil Prabhu, Lord of data, Master of bits, Warden of CPU Cycles, sits on the Iron Throne

## I. Project Abstract
Airlines delays are a common occurrence and an unfortunate part of travel today. It can happen for a number of reasons, e.g., weather delays, equipment failures, staff shortages, etc. When it does occur - it is a significant inconvenience to the passengers (i.e., wait times, unforeseen change of plans), the airlines (i.e., significant cost incurred, logistic adaptations), and the airports (i.e., gates are held up and additional airlines are delayed as a result). Airline delays can have a significant snowball effect. The purpose of this project is to use airline, weather, and airport weather station data to better predict airline delays (as defined as 15 minutes or more) using machine learning algorithms. Depending on the accuracy of our machine learning algorithms, we can share our findings of the significant drivers of airline delays to better forecast future delays and hopefully reduce the impact on all involved parties. 

**Abstract doesn't really represent the goal you've set for yourselves by the time you finish reading the notebook. In future you might even want to wait to so summary work until the end.**

## II. Introduction

The goal of this project is to develop a machine learning model that can predict whether a flight in the United States will be delayed or not. Before formalizing this task, it will be important to take a look at the data available and evaluate what would be feasible. 

This introduction section will set up the notebook, import the relevant data, and take a first glance at the different datasets that will be used to develop a model to predict flight delays.

#### I. Notebook Setup
Import relevant modules needed to run the code in this notebook.

In [0]:
## Import Relevant Modules
# General 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

# PySpark 
from pyspark.sql.functions import col,isnan,when,count
from pyspark.sql.functions import regexp_replace

# SQL Functions
from pyspark.sql import functions as f
from pyspark.sql.functions import monotonically_increasing_id
from pyspark.sql.functions import isnan, when, count, col, isnull, percent_rank
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType, NullType, ShortType, DateType, BooleanType, BinaryType, FloatType
from pyspark.sql import SQLContext
from pyspark.sql.window import Window
from pyspark.streaming import StreamingContext
from pyspark.sql import Row
from functools import reduce
from pyspark.sql.functions import rand,col,when,concat,substring,lit,udf,lower,sum as ps_sum,count as ps_count,row_number
from pyspark.sql.window import *
from pyspark.sql import DataFrame

# ML
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

#### II. Data Ingestion
Retrieve relevant parquet file paths and load into PySpark.

In [0]:
# Display and define where mids-w261 is located
data_BASE_DIR = "dbfs:/mnt/mids-w261/"
display(dbutils.fs.ls(f"{data_BASE_DIR}"))

path name size modificationTime dbfs:/mnt/mids-w261/HW5/ HW5/ 0 0 dbfs:/mnt/mids-w261/datasets_final_project/ datasets_final_project/ 0 0 dbfs:/mnt/mids-w261/datasets_final_project_2022/ datasets_final_project_2022/ 0 1656617686000

In [0]:
# Inspect the Mount's Final Project folder 
data_BASE_DIR = "dbfs:/mnt/mids-w261/datasets_final_project_2022/"
display(dbutils.fs.ls(f"{data_BASE_DIR}"))

path name size modificationTime dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/ parquet_airlines_data/ 0 1656618287000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_1y/ parquet_airlines_data_1y/ 0 1656630272000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_3m/ parquet_airlines_data_3m/ 0 1656630114000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_6m/ parquet_airlines_data_6m/ 0 1656630205000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/ parquet_weather_data/ 0 1656622074000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data_1y/ parquet_weather_data_1y/ 0 1656631614000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data_3m/ parquet_weather_data_3m/ 0 1656630651000 dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data_6m/ parquet_weather_data_6m/ 0 1656631047000 dbfs:/mnt/mids-w261/datasets_final_project_2022/stations_data/ stations_data/ 0 1656713663000

In [0]:
%sh du -h /dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data

435M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2015
427M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2016
437M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2017
574M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2018
595M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2019
143M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2020
198M	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data/YEAR=2021
2.8G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data


In [0]:
%sh du -h /dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/

4.7G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2015
4.6G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2016
4.8G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2017
4.7G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2018
4.8G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2019
4.7G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2020
4.7G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/YEAR=2021
33G	/dbfs/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data/


In [0]:
%sh du -h /dbfs/mnt/mids-w261/datasets_final_project_2022/stations_data/

53M	/dbfs/mnt/mids-w261/datasets_final_project_2022/stations_data/stations_with_neighbors.parquet
53M	/dbfs/mnt/mids-w261/datasets_final_project_2022/stations_data/


In [0]:
## Read in parquet files to be dataframes
# Airlines dataset
df_airlinesRAW = spark.read.parquet(f"{data_BASE_DIR}parquet_airlines_data_3m/")

# Weather dataset
df_weatherRAW = spark.read.parquet(f"{data_BASE_DIR}parquet_weather_data_3m/").filter(col('DATE') < "2015-04-01T00:00:00.000")

# Stations dataset 
df_stationsRAW = spark.read.parquet(f"{data_BASE_DIR}stations_data/*")

### III. Data Explanation

The below table states the four different datasets that will be used, their respective sizes, and where they were obtained.

| Dataset    | Size    | Source |
|------------|--------|--------|
| Airline    | 2.8 GB | [United States Department of Transportation](https://www.transtats.bts.gov/homepage.asp)  |
| Weather    | 33 GB  | [National Oceanic and Atmospheric Observatory Repository](https://www.ncei.noaa.gov/access/metadata/landing-page/bin/iso?id=gov.noaa.ncdc:C00679)    |
| Stations   | --    | Provided by W261 instructors  |
| Airport    | 5.6 MB | [Third-party Open Source Airport Data](https://davidmegginson.github.io/ourairports-data/airports.csv)   |

Given the large size of the airline and weather datasets, a subset (first quarter/three months of the year 2015) of the full dataset will be used to conduct initial explorations and understandings of the data at hand. As the models get developed, we will leverage the full datasets. 

Furthermore, the airport dataset is the only dataset that was sourced independently by the project team. This was done to gain more information about individual airports, which was determined to be needed while conducting initial exploratory data analysis. This will be expanded upon in the following sections. 

The following four subsections will provide initial insights on what information is included in the datasets to help inform the actual project task the team will work on.

#### I. Airlines Dataset Overview (RAW)

*Note: this is done on the data subset of Q1 2015*

The airlines dataset provides flight information in the United States. In particular it gives information on whether a flight was on time, delayed, cancelled, or diverted (more details in the information highlights section below). This dataset will be key in developing any model on flight delays, as it contains the data labels on whether or not a flight was on time, delayed, or cancelled. It is likely that the model will not consider flights that have been diverted because normally a flight diversion happens after a flight has taken off, and to predict a flight delay, only variables that can be known before a flight has taken off can be considered. This also means that in addition to variables on diverted flights, variables that speak to things that have happened when a flight lands will not be useful. The only variables that could be of use is whether or not a flight has been delayed, cancelled, and delayed by how many minutes, as these will be used in generating the appropriate labels the model will try to predict. 

In terms of missing data, there are certain columns that have many null values, but it looks like there is a logic to it.  For example, if a flight was not delayed it will not have information about how long the delay was. Some logical checks to ensure this is the case will be added to the data pipeline. One variable that may be very important for each observation is the tail number (i.e. the identificiation of the specific plane for the flight), which has a quite a number of missing values (16,380 out of 2,806,942). In theory this could be an important predictor on whether a flight may be delayed or cancelled, as this is the only indication on the condition of plane, but these observations likely will need to be filtered out because there is no confident way that the team would be able to know the condition of the plane without specific airfleet data that is likely to be confidential. 

Metadata:
- 2,806,942 rows (subset)/ 31,746,841 rows (full dataset)
- 109 columns (subset and full dataset) 
- Both numeric (integer and double) and string data types 

Information Highlights:
- Each record pertains to a specific flight 
- Flight date (date, quarter, month, day, day of week, year —> last column)
- Carrier information (airline IDS, tail number, flight number)
- Origin information (airport, city, state)
- Destination information (airport, city, state)
- Departure performance (time, delay, taxi out time, wheels off time)
- Arrival performance (wheels on, taxi in time, time, delay)
- Cancellation (flight cancelled, diverted flight)
- Flight summaries (elapsed flight time, no. flights, distance)
- Delay cause (in minutes —> carrier, weather, national air system, security, late aircraft)
- Gate return information at origin airport (gate departure time, total ground time away from gate for gate return or cancelled flight, longest time away from gate for gate return or cancelled flight)
- Diverted airport information - in case of diversion (for up to 4 airports: number, destination, elapsed time, delay, distance, airport, wheels on, ground time away)

In [0]:
# Get Row and Column Count for RAW Airlines Dataset
rows1 = df_airlinesRAW.count()
columns1 = len(df_airlinesRAW.columns)
print('RAW Airlines Dataset:')
print(f'Number of rows: {rows1}')
print(f'Number of columns: {columns1}')

RAW Airlines Dataset:
Number of rows: 2806942
Number of columns: 109


In [0]:
# Quick Look at Airlines dataset
display(df_airlinesRAW)

QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN_CITY_MARKET_ID ORIGIN ORIGIN_CITY_NAME ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM ORIGIN_WAC DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST_CITY_MARKET_ID DEST DEST_CITY_NAME DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM DEST_WAC CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK TAXI_OUT WHEELS_OFF WHEELS_ON TAXI_IN CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 ARR_DELAY_GROUP ARR_TIME_BLK CANCELLED CANCELLATION_CODE DIVERTED CRS_ELAPSED_TIME ACTUAL_ELAPSED_TIME AIR_TIME FLIGHTS DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY FIRST_DEP_TIME TOTAL_ADD_GTIME LONGEST_ADD_GTIME DIV_AIRPORT_LANDINGS DIV_REACHED_DEST DIV_ACTUAL_ELAPSED_TIME DIV_ARR_DELAY DIV_DISTANCE DIV1_AIRPORT DIV1_AIRPORT_ID DIV1_AIRPORT_SEQ_ID DIV1_WHEELS_ON DIV1_TOTAL_GTIME DIV1_LONGEST_GTIME DIV1_WHEELS_OFF DIV1_TAIL_NUM DIV2_AIRPORT DIV2_AIRPORT_ID DIV2_AIRPORT_SEQ_ID DIV2_WHEELS_ON DIV2_TOTAL_GTIME DIV2_LONGEST_GTIME DIV2_WHEELS_OFF DIV2_TAIL_NUM DIV3_AIRPORT DIV3_AIRPORT_ID DIV3_AIRPORT_SEQ_ID DIV3_WHEELS_ON DIV3_TOTAL_GTIME DIV3_LONGEST_GTIME DIV3_WHEELS_OFF DIV3_TAIL_NUM DIV4_AIRPORT DIV4_AIRPORT_ID DIV4_AIRPORT_SEQ_ID DIV4_WHEELS_ON DIV4_TOTAL_GTIME DIV4_LONGEST_GTIME DIV4_WHEELS_OFF DIV4_TAIL_NUM DIV5_AIRPORT DIV5_AIRPORT_ID DIV5_AIRPORT_SEQ_ID DIV5_WHEELS_ON DIV5_TOTAL_GTIME DIV5_LONGEST_GTIME DIV5_WHEELS_OFF DIV5_TAIL_NUM YEAR 1 2 19 4 2015-02-19 AA 19805 AA N520AA 323 15016 1501603 31123 STL St. Louis, MO MO 29 Missouri 64 11298 1129803 30194 DFW Dallas/Fort Worth, TX TX 48 Texas 74 901 949 48.0 48.0 1.0 3 0900-0959 23.0 1012 1130 5.0 1058 1135 37.0 37.0 1.0 2 1000-1059 0.0 null 0.0 117.0 106.0 78.0 1.0 550.0 3 0.0 5.0 0.0 0.0 32.0 null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 20 5 2015-02-20 AA 19805 AA N4XUAA 323 15016 1501603 31123 STL St. Louis, MO MO 29 Missouri 64 11298 1129803 30194 DFW Dallas/Fort Worth, TX TX 48 Texas 74 901 855 -6.0 0.0 0.0 -1 0900-0959 11.0 906 1033 26.0 1058 1059 1.0 1.0 0.0 0 1000-1059 0.0 null 0.0 117.0 124.0 87.0 1.0 550.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 21 6 2015-02-21 AA 19805 AA N486AA 323 15016 1501603 31123 STL St. Louis, MO MO 29 Missouri 64 11298 1129803 30194 DFW Dallas/Fort Worth, TX TX 48 Texas 74 901 1018 77.0 77.0 1.0 5 0900-0959 11.0 1029 1207 5.0 1058 1212 74.0 74.0 1.0 4 1000-1059 0.0 null 0.0 117.0 114.0 98.0 1.0 550.0 3 27.0 0.0 0.0 0.0 47.0 null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 22 7 2015-02-22 AA 19805 AA N456AA 323 15016 1501603 31123 STL St. Louis, MO MO 29 Missouri 64 11298 1129803 30194 DFW Dallas/Fort Worth, TX TX 48 Texas 74 901 853 -8.0 0.0 0.0 -1 0900-0959 9.0 902 1036 14.0 1058 1050 -8.0 0.0 0.0 -1 1000-1059 0.0 null 0.0 117.0 117.0 94.0 1.0 550.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 23 1 2015-02-23 AA 19805 AA N4XTAA 323 15016 1501603 31123 STL St. Louis, MO MO 29 Missouri 64 11298 1129803 30194 DFW Dallas/Fort Worth, TX TX 48 Texas 74 901 null null null null n

In [0]:
# Get Information on Datatypes for Airlines Dataset
print('RAW Airlines Dataset Schema')
print()
df_airlinesRAW.printSchema()

RAW Airlines Dataset Schema

root
 |-- QUARTER: integer (nullable = true)
 |-- MONTH: integer (nullable = true)
 |-- DAY_OF_MONTH: integer (nullable = true)
 |-- DAY_OF_WEEK: integer (nullable = true)
 |-- FL_DATE: string (nullable = true)
 |-- OP_UNIQUE_CARRIER: string (nullable = true)
 |-- OP_CARRIER_AIRLINE_ID: integer (nullable = true)
 |-- OP_CARRIER: string (nullable = true)
 |-- TAIL_NUM: string (nullable = true)
 |-- OP_CARRIER_FL_NUM: integer (nullable = true)
 |-- ORIGIN_AIRPORT_ID: integer (nullable = true)
 |-- ORIGIN_AIRPORT_SEQ_ID: integer (nullable = true)
 |-- ORIGIN_CITY_MARKET_ID: integer (nullable = true)
 |-- ORIGIN: string (nullable = true)
 |-- ORIGIN_CITY_NAME: string (nullable = true)
 |-- ORIGIN_STATE_ABR: string (nullable = true)
 |-- ORIGIN_STATE_FIPS: integer (nullable = true)
 |-- ORIGIN_STATE_NM: string (nullable = true)
 |-- ORIGIN_WAC: integer (nullable = true)
 |-- DEST_AIRPORT_ID: integer (nullable = true)
 |-- DEST_AIRPORT_SEQ_ID: integer (nullable =

In [0]:
# Count Null Values
df_airlinesRAWCols = df_airlinesRAW

print('Count of Null Values in RAW Airlines Dataset')

df_airlinesRAWNulls = df_airlinesRAW.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in df_airlinesRAWCols.columns])

display(df_airlinesRAWNulls)

Count of Null Values in RAW Airlines Dataset


#### II. Weather Dataset Overview (RAW)

This dataset contains weather readings for weather stations across the United States (for initial EDA, a subset of first quarter of 2015 was used). It is well known that intense weather conditions such as high winds or heavy snow can make it difficult for pilots to navigate a plane safely, which is why weather related delays are common. Weather delays is a category in the airlines dataset, further supporting the idea that weather related information could be useful in predicting flight delays and cancellations. 

It is also important to note that the weather dataset does have multiple columns where the majority values are null (some almost 30 million out of ~30.5 million). But it looks like there are less missing for the hourly weather readings which may be of greater use for this project in any case because the weather around the time of planned departure is important. To handle the missing data more investigation needs to be done on which relevant stations have missing data, and if there are any areas nearby from which the weather can be inferred. Depending on this, it can be decided whether to drop or impute the missing data. 

Metadata:
- 30,528,602 rows (subset)/630,904,436 rows (full dataset)
- 124 columns (full dataset)

Information Highlights
- date
- station information (ID, GPS coordinates, elevation, name)
- columns giving information at hourly, daily, and monthly time intervals 
- variables on temperature, pressure change, humidity, sky conditions, visibility, and wind
- sunrise, sunset
- information on backup equipment used
- date on wind equipment change

In [0]:
# Get Row and Column Count for RAW Weather Dataset
rows2 = df_weatherRAW.count()
columns2 = len(df_weatherRAW.columns)
print('RAW Weather Dataset:')
print(f'Number of rows: {rows2}')
print(f'Number of columns: {columns2}')

RAW Weather Dataset:
Number of rows: 30528602
Number of columns: 124


In [0]:
#Quick Look at Weather dataset
display(df_weatherRAW)

STATION DATE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE SOURCE HourlyAltimeterSetting HourlyDewPointTemperature HourlyDryBulbTemperature HourlyPrecipitation HourlyPresentWeatherType HourlyPressureChange HourlyPressureTendency HourlyRelativeHumidity HourlySkyConditions HourlySeaLevelPressure HourlyStationPressure HourlyVisibility HourlyWetBulbTemperature HourlyWindDirection HourlyWindGustSpeed HourlyWindSpeed Sunrise Sunset DailyAverageDewPointTemperature DailyAverageDryBulbTemperature DailyAverageRelativeHumidity DailyAverageSeaLevelPressure DailyAverageStationPressure DailyAverageWetBulbTemperature DailyAverageWindSpeed DailyCoolingDegreeDays DailyDepartureFromNormalAverageTemperature DailyHeatingDegreeDays DailyMaximumDryBulbTemperature DailyMinimumDryBulbTemperature DailyPeakWindDirection DailyPeakWindSpeed DailyPrecipitation DailySnowDepth DailySnowfall DailySustainedWindDirection DailySustainedWindSpeed DailyWeather MonthlyAverageRH MonthlyDaysWithGT001Precip MonthlyDaysWithGT010Precip MonthlyDaysWithGT32Temp MonthlyDaysWithGT90Temp MonthlyDaysWithLT0Temp MonthlyDaysWithLT32Temp MonthlyDepartureFromNormalAverageTemperature MonthlyDepartureFromNormalCoolingDegreeDays MonthlyDepartureFromNormalHeatingDegreeDays MonthlyDepartureFromNormalMaximumTemperature MonthlyDepartureFromNormalMinimumTemperature MonthlyDepartureFromNormalPrecipitation MonthlyDewpointTemperature MonthlyGreatestPrecip MonthlyGreatestPrecipDate MonthlyGreatestSnowDepth MonthlyGreatestSnowDepthDate MonthlyGreatestSnowfall MonthlyGreatestSnowfallDate MonthlyMaxSeaLevelPressureValue MonthlyMaxSeaLevelPressureValueDate MonthlyMaxSeaLevelPressureValueTime MonthlyMaximumTemperature MonthlyMeanTemperature MonthlyMinSeaLevelPressureValue MonthlyMinSeaLevelPressureValueDate MonthlyMinSeaLevelPressureValueTime MonthlyMinimumTemperature MonthlySeaLevelPressure MonthlyStationPressure MonthlyTotalLiquidPrecipitation MonthlyTotalSnowfall MonthlyWetBulb AWND CDSD CLDD DSNW HDSD HTDD NormalsCoolingDegreeDay NormalsHeatingDegreeDay ShortDurationEndDate005 ShortDurationEndDate010 ShortDurationEndDate015 ShortDurationEndDate020 ShortDurationEndDate030 ShortDurationEndDate045 ShortDurationEndDate060 ShortDurationEndDate080 ShortDurationEndDate100 ShortDurationEndDate120 ShortDurationEndDate150 ShortDurationEndDate180 ShortDurationPrecipitationValue005 ShortDurationPrecipitationValue010 ShortDurationPrecipitationValue015 ShortDurationPrecipitationValue020 ShortDurationPrecipitationValue030 ShortDurationPrecipitationValue045 ShortDurationPrecipitationValue060 ShortDurationPrecipitationValue080 ShortDurationPrecipitationValue100 ShortDurationPrecipitationValue120 ShortDurationPrecipitationValue150 ShortDurationPrecipitationValue180 REM BackupDirection BackupDistance BackupDistanceUnit BackupElements BackupElevation BackupEquipment BackupLatitude BackupLongitude BackupName WindEquipmentChangeDate YEAR 52652099999 2015-01-01T02:00:00 39.0833333 100.2833333 1462.0 ZHANGYE, CH FM-12 4 null -1 3 null null +0.04 7 83 null 30.72 25.45 null 2 290 null 4 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null SYN06452652 32/// 92902 11163 21186 38618 40403 57015 333 00051 11045= null null null null null null null null null null 2015 52652099999 2015-01-01T05:00:00 39.0833333 100.2833333 1462.0 ZHANGYE, CH FM-12 4 null -1 4 null null +0.01 7 77 null 30.68 null null null 320 null 4 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null nu

In [0]:
# Get Information on Datatypes for Weather Dataset
print('RAW Weather Dataset Schema')
print()
df_weatherRAW.printSchema()

RAW Weather Dataset Schema

root
 |-- STATION: string (nullable = true)
 |-- DATE: string (nullable = true)
 |-- LATITUDE: string (nullable = true)
 |-- LONGITUDE: string (nullable = true)
 |-- ELEVATION: string (nullable = true)
 |-- NAME: string (nullable = true)
 |-- REPORT_TYPE: string (nullable = true)
 |-- SOURCE: string (nullable = true)
 |-- HourlyAltimeterSetting: string (nullable = true)
 |-- HourlyDewPointTemperature: string (nullable = true)
 |-- HourlyDryBulbTemperature: string (nullable = true)
 |-- HourlyPrecipitation: string (nullable = true)
 |-- HourlyPresentWeatherType: string (nullable = true)
 |-- HourlyPressureChange: string (nullable = true)
 |-- HourlyPressureTendency: string (nullable = true)
 |-- HourlyRelativeHumidity: string (nullable = true)
 |-- HourlySkyConditions: string (nullable = true)
 |-- HourlySeaLevelPressure: string (nullable = true)
 |-- HourlyStationPressure: string (nullable = true)
 |-- HourlyVisibility: string (nullable = true)
 |-- HourlyWe

In [0]:
# Count Null Values for Weather Dataset
df_weatherRAWCols = df_weatherRAW

print('Count of Null Values in RAW Weather Dataset')

df_weatherRAWNulls = df_weatherRAW.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in df_weatherRAWCols.columns])

display(df_weatherRAWNulls)

Count of Null Values in RAW Weather Dataset


STATION DATE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE SOURCE HourlyAltimeterSetting HourlyDewPointTemperature HourlyDryBulbTemperature HourlyPrecipitation HourlyPresentWeatherType HourlyPressureChange HourlyPressureTendency HourlyRelativeHumidity HourlySkyConditions HourlySeaLevelPressure HourlyStationPressure HourlyVisibility HourlyWetBulbTemperature HourlyWindDirection HourlyWindGustSpeed HourlyWindSpeed Sunrise Sunset DailyAverageDewPointTemperature DailyAverageDryBulbTemperature DailyAverageRelativeHumidity DailyAverageSeaLevelPressure DailyAverageStationPressure DailyAverageWetBulbTemperature DailyAverageWindSpeed DailyCoolingDegreeDays DailyDepartureFromNormalAverageTemperature DailyHeatingDegreeDays DailyMaximumDryBulbTemperature DailyMinimumDryBulbTemperature DailyPeakWindDirection DailyPeakWindSpeed DailyPrecipitation DailySnowDepth DailySnowfall DailySustainedWindDirection DailySustainedWindSpeed DailyWeather MonthlyAverageRH MonthlyDaysWithGT001Precip MonthlyDaysWithGT010Precip MonthlyDaysWithGT32Temp MonthlyDaysWithGT90Temp MonthlyDaysWithLT0Temp MonthlyDaysWithLT32Temp MonthlyDepartureFromNormalAverageTemperature MonthlyDepartureFromNormalCoolingDegreeDays MonthlyDepartureFromNormalHeatingDegreeDays MonthlyDepartureFromNormalMaximumTemperature MonthlyDepartureFromNormalMinimumTemperature MonthlyDepartureFromNormalPrecipitation MonthlyDewpointTemperature MonthlyGreatestPrecip MonthlyGreatestPrecipDate MonthlyGreatestSnowDepth MonthlyGreatestSnowDepthDate MonthlyGreatestSnowfall MonthlyGreatestSnowfallDate MonthlyMaxSeaLevelPressureValue MonthlyMaxSeaLevelPressureValueDate MonthlyMaxSeaLevelPressureValueTime MonthlyMaximumTemperature MonthlyMeanTemperature MonthlyMinSeaLevelPressureValue MonthlyMinSeaLevelPressureValueDate MonthlyMinSeaLevelPressureValueTime MonthlyMinimumTemperature MonthlySeaLevelPressure MonthlyStationPressure MonthlyTotalLiquidPrecipitation MonthlyTotalSnowfall MonthlyWetBulb AWND CDSD CLDD DSNW HDSD HTDD NormalsCoolingDegreeDay NormalsHeatingDegreeDay ShortDurationEndDate005 ShortDurationEndDate010 ShortDurationEndDate015 ShortDurationEndDate020 ShortDurationEndDate030 ShortDurationEndDate045 ShortDurationEndDate060 ShortDurationEndDate080 ShortDurationEndDate100 ShortDurationEndDate120 ShortDurationEndDate150 ShortDurationEndDate180 ShortDurationPrecipitationValue005 ShortDurationPrecipitationValue010 ShortDurationPrecipitationValue015 ShortDurationPrecipitationValue020 ShortDurationPrecipitationValue030 ShortDurationPrecipitationValue045 ShortDurationPrecipitationValue060 ShortDurationPrecipitationValue080 ShortDurationPrecipitationValue100 ShortDurationPrecipitationValue120 ShortDurationPrecipitationValue150 ShortDurationPrecipitationValue180 REM BackupDirection BackupDistance BackupDistanceUnit BackupElements BackupElevation BackupEquipment BackupLatitude BackupLongitude BackupName WindEquipmentChangeDate YEAR 0 0 241154 241154 241154 241154 0 0 14077864 5363413 651063 26596147 26599574 22102547 21803877 5371495 14476375 19468244 15025512 10576036 15281390 4351048 28340702 4044614 30377170 30377160 30499862 30423710 30499631 30499896 30438234 30499862 30437818 30423710 30434429 30423710 30423681 30423689 30440690 30436954 30423616 30490669 30491778 30437703 30436892 30434968 30528602 30525362 30525362 30525420 30525423 30525420 30525420 30525496 30525517 30525517 30525496 30525496 30525827 30528602 30525814 30525919 30527924 30528086 30527915 30528017 30525836 30525835 30525835 30525371 30525371 30525839 30525838 30525838 30525371 30525871 30525859 30525468 30528018 30528602 30525927 30525457 30525433 30527608 30525645 30525433 30525463 30525463 30526151 30526151 30526151 30526151 30526151 30526151 30526151 30526152 30526152 30526151 30526151 30526157 30526151 30526151 30526151 30526151 30526151 30526151 30526151 30526152 30526152 30526151 30526151 30526157 4021654 30010429 30007610 30007610 30001132 30126564 30020963 30133883 30133883 29983831 28669085 0

#### III. Station Dataset Overview (RAW)

The station dataset gives information collected at weather stations located closeby airport. It gives information on where the station is located and will be useful in joining with the weather dataset to get the relevant weather readings for each airport at the specific moment in time. Further information on joining tables is in data pipeline section V. There are no null values. 

Metadata:
- 5,004,169 rows
- 12 columns

Highlights of Column Information:
- station ID information 
- GPS coordinates of station and neighboring station
- neighbor_name has (sometimes) the name of the nearest airport

In [0]:
# Get Row and Column Count for RAW Stations Dataset
rows3 = df_stationsRAW.count()
columns3 = len(df_stationsRAW.columns)
print('RAW Weather Dataset:')
print(f'Number of rows: {rows3}')
print(f'Number of columns: {columns3}')

RAW Weather Dataset:
Number of rows: 5004169
Number of columns: 12


In [0]:
# Quick look at stations dataset 
display(df_stationsRAW)

usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor 690020 93218 69002093218 36.0 -121.233 69002093218 JOLON HUNTER LIGGETT MIL RES CA KHGT 36.0 -121.233 0.0 690020 93218 69002093218 36.0 -121.233 69007093217 FRITZSCHE AAF CA KOAR 36.683 -121.767 55.73024537916726 690020 93218 69002093218 36.0 -121.233 69014093101 EL TORO MCAS CA KNZJ 33.667 -117.733 255.49106220353934 690020 93218 69002093218 36.0 -121.233 70027127506 BARROW POINT BARROW AK KPBA 71.333 -156.65 2750.4353299559803 690020 93218 69002093218 36.0 -121.233 70045027512 LONELY AK LNI 70.917 -153.25 2676.3554370627153 690020 93218 69002093218 36.0 -121.233 70063027403 OLIKTOK POW 2 AK POLI 70.5 -149.883 2604.050248854232 690020 93218 69002093218 36.0 -121.233 70063526465 GALBRAITH LAKE AIRPORT AK PAGB 68.479 -149.49 2490.9756094472277 690020 93218 69002093218 36.0 -121.233 70063627405 PRUDHOE BAY AK PAUD 70.25 -148.333 2568.180281844432 690020 93218 69002093218 36.0 -121.233 70104626418 CENTRAL AIRPORT AK PACE 65.567 -144.765 2254.5584891291946 690020 93218 69002093218 36.0 -121.233 70119526625 SHISHMAREF/NEW AIRPORT AK PASH 66.25 -166.089 2743.6881828292408 690020 93218 69002093218 36.0 -121.233 70121326638 POINT LAY LIZ 2 AK PIZ 69.733 -163.017 2796.6187763021226 690020 93218 69002093218 36.0 -121.233 70148626642 KIVALINA AIRPORT AK PAVL 67.732 -164.548 2755.8847615355235 690020 93218 69002093218 36.0 -121.233 70162026508 UMIAT AK PAUM 69.367 -152.133 2580.421414177685 690020 93218 69002093218 36.0 -121.233 70171900490 SHUNGNAK AIRPORT AK PAGH 66.888 -157.162 2560.459862643483 690020 93218 69002093218 36.0 -121.233 70174526480 CHANDALAR LAKE AIRPORT AK PALR 67.511 -148.493 2423.3408124753164 690020 93218 69002093218 36.0 -121.233 70179326524 MANLEY HOT SPRINGS AK PAML 64.999 -150.638 2336.6091618691917 690020 93218 69002093218 36.0 -121.233 70199526628 CAPE DARBY REMOT COM OUTLT AK PAGL 64.55 -163.007 2610.7849480759573 690020 93218 69002093218 36.0 -121.233 70206026632 NORTHEAST CAPE AK KOHC 63.317 -168.967 2740.2899674712785 690020 93218 69002093218 36.0 -121.233 70222326602 KOYUK AIRPORT AK PAKK 64.935 -161.155 2576.6261990332778 690020 93218 69002093218 36.0 -121.233 70231226555 FAREWELL LAKE SEAPLANE BASE AK PAFK 62.543 -153.623 2293.7430034471354 690020 93218 69002093218 36.0 -121.233 70249526547 HAYES RIVER AIRPORT AK PAHZ 61.983 -152.083 2230.946084519868 690020 93218 69002093218 36.0 -121.233 70255026514 SKWENTNA AIRPORT AK PASW 61.977 -151.217 2209.0623964277706 690020 93218 69002093218 36.0 -121.233 70264026414 SUMMIT AK PAST 63.331 -149.127 2223.352307308065 690020 93218 69002093218 36.0 -121.233 70264726499 HEALY RIVER AIRPORT AK PAHV 63.866 -148.969 2246.1213363715397 690020 93218 69002093218 36.0 -121.233 70264846406 CANTWELL AIRPORT AK PATW 63.391 -148.956 2222.52653340686 690020 93218 69002093218 36.0 -121.233 70267526484 PAXSON AIRPORT AK PAXK 63.032 -145.498 2131.3748228756726 690020 93218 69002093218 36.0 -121.233 70269596402 JONESVILLE MINE AIRPORT AK PAJV 61.714 -148.909 2140.8509123873396 690020 93218 69002093218 36.0 -121.233 70271126439 SHEEP MOUNTAIN AIRPORT AK PASP 61.812 -147.507 2112.749500893187 690020 93218 69002093218 36.0 -121.233 70274526560 WILLOW AIRPORT AK PAUO 61.748 -150.054 2170.093644623675 690020 93218 69002093218 36.0 -121.233 70275026442 NATIONAL WEATHER SERVICE OFFI AK PAVW 61.13 -146.352 2052.4465612834106 690020 93218 69002093218 36.0 -121.233 70275546404 MCCARTHY AIRPORT AK PAMX 61.437 -142.904 1993.3299561949077 690020 93218 69002093218 36.0 -121.233 70275726444 WHITTIER AIRPORT AK PAWR 60.783 -148.733 2092.9535147837305 690020 93218 69002093218 36.0 -121.233 70291346402 DEVILS MOUNTAIN LODGE AIRPORT AK PABN 62.402 -142.995 2047.8132237563839 690020 93218 69002093218 36.0 -121.233 70291526486 DUFFY'S TAVERN AIRPORT AK PADT 62.709 -143.981 2083.812325469856 690020 93218 69002093218 36.0 -121.233 70292326440 TANACROSS AK TSG 63.383 -143.333 2

In [0]:
# Get Information on Datatypes for Weather Dataset
print('RAW Stations Dataset Schema')
print()
df_stationsRAW.printSchema()

RAW Stations Dataset Schema

root
 |-- usaf: string (nullable = true)
 |-- wban: string (nullable = true)
 |-- station_id: string (nullable = true)
 |-- lat: double (nullable = true)
 |-- lon: double (nullable = true)
 |-- neighbor_id: string (nullable = true)
 |-- neighbor_name: string (nullable = true)
 |-- neighbor_state: string (nullable = true)
 |-- neighbor_call: string (nullable = true)
 |-- neighbor_lat: double (nullable = true)
 |-- neighbor_lon: double (nullable = true)
 |-- distance_to_neighbor: double (nullable = true)



In [0]:
# Count Null Values for Weather Dataset
df_stationsRAWCols = df_stationsRAW

print('Count of Null Values in RAW Airlines Dataset')

df_stationsRAWNulls = df_stationsRAW.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in df_stationsRAWCols.columns])

display(df_stationsRAWNulls)

Count of Null Values in RAW Airlines Dataset


usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor 0 0 0 0 0 0 0 0 0 0 0 0

#### IV. Airport Data (RAW/Third Party Data)

The airport dataset gives information on global airports. This outside dataset will provide a common key such as GPS code or longitude/latitude which will allow us to join airport data with weather data. The dataset is a third-party open-source data set and was last updated October 30th, 2022.

Metadata:
- 73,814 rows
- 18 columns

Highlights of Column Information:
- Airport code and name
- GPS Code
- Longitude and latitude coordinates of airport

In [0]:
# df_airports = spark.read.format("delta").load("https://davidmegginson.github.io/ourairports-data/airports.csv")
# display(df_airports)
df_airports = pd.read_csv("https://davidmegginson.github.io/ourairports-data/airports.csv").astype(str)
df_airports = spark.createDataFrame(df_airports)

In [0]:
# Get Row and Column Count for RAW Stations Dataset
rows4 = df_airports.count()
columns4 = len(df_airports.columns)
print('Airport Dataset:')
print(f'Number of rows: {rows4}')
print(f'Number of columns: {columns4}')

display(df_airports)

Airport Dataset:
Number of rows: 73814
Number of columns: 18


id ident type name latitude_deg longitude_deg elevation_ft continent iso_country iso_region municipality scheduled_service gps_code iata_code local_code home_link wikipedia_link keywords 6523 00A heliport Total Rf Heliport 40.07080078125 -74.93360137939453 11.0 nan US US-PA Bensalem no 00A nan 00A nan nan nan 323361 00AA small_airport Aero B Ranch Airport 38.704022 -101.473911 3435.0 nan US US-KS Leoti no 00AA nan 00AA nan nan nan 6524 00AK small_airport Lowell Field 59.947733 -151.692524 450.0 nan US US-AK Anchor Point no 00AK nan 00AK nan nan nan 6525 00AL small_airport Epps Airpark 34.86479949951172 -86.77030181884766 820.0 nan US US-AL Harvest no 00AL nan 00AL nan nan nan 6526 00AR closed Newport Hospital & Clinic Heliport 35.6087 -91.254898 237.0 nan US US-AR Newport no nan nan nan nan nan 00AR 322127 00AS small_airport Fulton Airport 34.9428028 -97.8180194 1100.0 nan US US-OK Alex no 00AS nan 00AS nan nan nan 6527 00AZ small_airport Cordes Airport 34.305599212646484 -112.16500091552734 3810.0 nan US US-AZ Cordes no 00AZ nan 00AZ nan nan nan 6528 00CA small_airport Goldstone (GTS) Airport 35.35474 -116.885329 3038.0 nan US US-CA Barstow no 00CA nan 00CA nan nan nan 324424 00CL small_airport Williams Ag Airport 39.427188 -121.763427 87.0 nan US US-CA Biggs no 00CL nan 00CL nan nan nan 322658 00CN heliport Kitchen Creek Helibase Heliport 32.7273736 -116.4597417 3350.0 nan US US-CA Pine Valley no 00CN nan 00CN nan nan nan 6529 00CO closed Cass Field 40.622202 -104.344002 4830.0 nan US US-CO Briggsdale no nan nan nan nan nan 00CO 6531 00FA small_airport Grass Patch Airport 28.64550018310547 -82.21900177001953 53.0 nan US US-FL Bushnell no 00FA nan 00FA nan nan nan 6532 00FD closed Ringhaver Heliport 28.8466 -82.345398 25.0 nan US US-FL Riverview no nan nan nan nan nan 00FD 6533 00FL small_airport River Oak Airport 27.230899810791016 -80.96920013427734 35.0 nan US US-FL Okeechobee no 00FL nan 00FL nan nan nan 6534 00GA small_airport Lt World Airport 33.76750183105469 -84.06829833984375 700.0 nan US US-GA Lithonia no 00GA nan 00GA nan nan nan 6535 00GE heliport Caffrey Heliport 33.887982 -84.736983 957.0 nan US US-GA Hiram no 00GE nan 00GE nan nan nan 6536 00HI heliport Kaupulehu Heliport 19.832881 -155.978347 43.0 OC US US-HI Kailua-Kona no 00HI nan 00HI nan nan nan 6537 00ID small_airport Delta Shores Airport 48.145301818847656 -116.21399688720705 2064.0 nan US US-ID Clark Fork no 00ID nan 00ID nan nan nan 322581 00IG small_airport Goltl Airport 39.724028 -101.395994 3359.0 nan US US-KS McDonald no 00IG nan 00IG nan nan nan 6538 00II closed Bailey Generation Station Heliport 41.644501 -87.122803 600.0 nan US US-IN Chesterton no nan nan nan nan nan 00II 6539 00IL small_airport Hammer Airport 41.978401 -89.560402 840.0 nan US US-IL Polo no 00IL nan 00IL nan nan Radio Ranch 6540 00IN heliport St Mary Medical Center Heliport 41.51139831542969 -87.2605972290039 634.0 nan US US-IN Hobart no 00IN nan 00IN nan nan nan 6541 00IS small_airport Hayenga's Cant Find Farms Airport 40.02560043334961 -89.1229019165039 820.0 nan US US-IL Kings no 00IS nan 00IS nan nan nan 6542 00KS small_airport Hayden Farm Airport 38.72779846191406 -94.93049621582033 1100.0 nan US US-KS Gardner no 00KS nan 00KS nan nan nan 6543 00KY small_airport Robbins Roost Airport 37.409400939941406 -84.61969757080078 1265.0 nan US US-KY Stanford no 00KY nan 00KY nan nan nan 45437 00LA heliport Shell Chemical East Site Heliport 30.191944 -90.980833 15.0 nan US US-LA Gonzales no 00LA nan 00LA nan nan nan 6544 00LL heliport Ac & R Components Heliport 39.66529846191406 -89.70559692382812 600.0 nan US US-IL Chatham no 00LL nan 00LL nan nan nan 6545 00LS small_airport Lejeune Airport 30.136299 -92.429398 12.0 nan US US-LA Crowley no 00LS nan 00LS nan nan nan 6546 00MD small_airport Slater Field 38.75709915161133 -75.75379943847656 45.0 nan US US-MD Federalsburg no 00MD nan 00MD nan nan nan 6547 00MI heliport Dow Chemical Heliport 43.94940185546875 -86.41670227050781 588.0 nan

## III. Exploratory Data Analysis (EDA)

We will complete an initial EDA to get a better understanding of the data. This initial EDA will help inform the next phases of the project and will consist of a few summary tables of a few key variables.

### I. EDA to Inform Project Question

In [0]:
df_airlinesRAW.createOrReplaceTempView('airlines')

# Number of flights by origin airport
df_origin = sqlContext.sql("""
WITH cte as (select 
             a.ORIGIN,
             a.ORIGIN_WAC,
             count(a.ORIGIN_WAC) as count_origin_wac, 
             CAST(avg(a.dep_delay) as DECIMAL(8,2)) as avg_departure_delay,
             CAST(avg(a.arr_delay) as DECIMAL(8,2)) as avg_arrival_delay
             from airlines as a
             group by 1, 2
             order by 3 desc, 4 desc)
 
select 
*
from cte  
""")

# Number of flights by airline
df_carrier = sqlContext.sql("""
WITH cte as (select 
             a.OP_UNIQUE_CARRIER,
             a.OP_CARRIER_AIRLINE_ID,
             a.OP_CARRIER,
             count(a.OP_CARRIER) as count_carrier,
             CAST(avg(a.dep_delay) as DECIMAL(8,2)) as avg_departure_delay,
             CAST(avg(a.arr_delay) as DECIMAL(8,2)) as avg_arrival_delay
             from airlines as a
             group by 1, 2, 3
             order by 4 desc, 5 desc)
 
select 
*
from cte 
""")

# Delays by Plane/Tail Number
df_plane = sqlContext.sql("""
WITH cte as (select 
             a.tail_num,
             case
             when a.cancelled = 1 then 'Cancelled'
             when a.cancelled = 0  and a.dep_del15 = 1 then 'Delayed'
             end as flight_status,
             count(tail_num) as count_flights,
             CAST(avg(a.dep_delay) as DECIMAL(8,2)) as avg_departure_delay,
             CAST(avg(a.arr_delay) as DECIMAL(8,2)) as avg_arrival_delay
             from airlines as a
             group by 1, 2
             order by 1, 2, 4 desc)
 
select 
*
from cte 
""")

display(df_origin)
display(df_carrier)
display(df_plane)

 
# |-- QUARTER: integer (nullable = true)
#  |-- MONTH: integer (nullable = true)
#  |-- DAY_OF_MONTH: integer (nullable = true)
#  |-- DAY_OF_WEEK: integer (nullable = true)
#  |-- FL_DATE: string (nullable = true)
#  |-- OP_UNIQUE_CARRIER: string (nullable = true)
#  |-- OP_CARRIER_AIRLINE_ID: integer (nullable = true)
#  |-- OP_CARRIER: string (nullable = true)
#  |-- TAIL_NUM: string (nullable = true)
#  |-- OP_CARRIER_FL_NUM: integer (nullable = true)
#  |-- ORIGIN_AIRPORT_ID: integer (nullable = true)
#  |-- ORIGIN_AIRPORT_SEQ_ID: integer (nullable = true)
#  |-- ORIGIN_CITY_MARKET_ID: integer (nullable = true)
#  |-- ORIGIN: string (nullable = true)
#  |-- ORIGIN_CITY_NAME: string (nullable = true)
#  |-- ORIGIN_STATE_ABR: string (nullable = true)
#  |-- ORIGIN_STATE_FIPS: integer (nullable = true)
#  |-- ORIGIN_STATE_NM: string (nullable = true)
#  |-- ORIGIN_WAC: integer (nullable = true)
#  |-- DEST_AIRPORT_ID: integer (nullable = true)
#  |-- DEST_AIRPORT_SEQ_ID: integer (nullable = true)
#  |-- DEST_CITY_MARKET_ID: integer (nullable = true)
#  |-- DEST: string (nullable = true)
#  |-- DEST_CITY_NAME: string (nullable = true)
#  |-- DEST_STATE_ABR: string (nullable = true)
#  |-- DEST_STATE_FIPS: integer (nullable = true)
#  |-- DEST_STATE_NM: string (nullable = true)
#  |-- DEST_WAC: integer (nullable = true)
#  |-- CRS_DEP_TIME: integer (nullable = true)
#  |-- DEP_TIME: integer (nullable = true)
#  |-- DEP_DELAY: double (nullable = true)
#  |-- DEP_DELAY_NEW: double (nullable = true)
#  |-- DEP_DEL15: double (nullable = true)
#  |-- DEP_DELAY_GROUP: integer (nullable = true)
#  |-- DEP_TIME_BLK: string (nullable = true)
#  |-- TAXI_OUT: double (nullable = true)
#  |-- WHEELS_OFF: integer (nullable = true)
#  |-- WHEELS_ON: integer (nullable = true)
#  |-- TAXI_IN: double (nullable = true)
#  |-- CRS_ARR_TIME: integer (nullable = true)
#  |-- ARR_TIME: integer (nullable = true)
#  |-- ARR_DELAY: double (nullable = true)
#  |-- ARR_DELAY_NEW: double (nullable = true)
#  |-- ARR_DEL15: double (nullable = true)
#  |-- ARR_DELAY_GROUP: integer (nullable = true)
#  |-- ARR_TIME_BLK: string (nullable = true)
#  |-- CANCELLED: double (nullable = true)
#  |-- CANCELLATION_CODE: string (nullable = true)
#  |-- DIVERTED: double (nullable = true)
#  |-- CRS_ELAPSED_TIME: double (nullable = true)
#  |-- ACTUAL_ELAPSED_TIME: double (nullable = true)
#  |-- AIR_TIME: double (nullable = true)
#  |-- FLIGHTS: double (nullable = true)
#  |-- DISTANCE: double (nullable = true)
#  |-- DISTANCE_GROUP: integer (nullable = true)
#  |-- CARRIER_DELAY: double (nullable = true)
#  |-- WEATHER_DELAY: double (nullable = true)
#  |-- NAS_DELAY: double (nullable = true)
#  |-- SECURITY_DELAY: double (nullable = true)
#  |-- LATE_AIRCRAFT_DELAY: double (nullable = true)
#  |-- FIRST_DEP_TIME: integer (nullable = true)
#  |-- TOTAL_ADD_GTIME: double (nullable = true)
#  |-- LONGEST_ADD_GTIME: double (nullable = true)
#  |-- DIV_AIRPORT_LANDINGS: integer (nullable = true)
#  |-- DIV_REACHED_DEST: double (nullable = true)
#  |-- DIV_ACTUAL_ELAPSED_TIME: double (nullable = true)
#  |-- DIV_ARR_DELAY: double (nullable = true)
#  |-- DIV_DISTANCE: double (nullable = true)
#  |-- DIV1_AIRPORT: string (nullable = true)
#  |-- DIV1_AIRPORT_ID: integer (nullable = true)
#  |-- DIV1_AIRPORT_SEQ_ID: integer (nullable = true)
#  |-- DIV1_WHEELS_ON: integer (nullable = true)
#  |-- DIV1_TOTAL_GTIME: double (nullable = true)
#  |-- DIV1_LONGEST_GTIME: double (nullable = true)
#  |-- DIV1_WHEELS_OFF: integer (nullable = true)
#  |-- DIV1_TAIL_NUM: string (nullable = true)
#  |-- DIV2_AIRPORT: string (nullable = true)
#  |-- DIV2_AIRPORT_ID: string (nullable = true)
#  |-- DIV2_AIRPORT_SEQ_ID: string (nullable = true)
#  |-- DIV2_WHEELS_ON: string (nullable = true)
#  |-- DIV2_TOTAL_GTIME: string (nullable = true)
#  |-- DIV2_LONGEST_GTIME: string (nullable = true)
#  |-- DIV2_WHEELS_OFF: string (nullable = true)
#  |-- DIV2_TAIL_NUM: string (nullable = true)
#  |-- DIV3_AIRPORT: string (nullable = true)
#  |-- DIV3_AIRPORT_ID: string (nullable = true)
#  |-- DIV3_AIRPORT_SEQ_ID: string (nullable = true)
#  |-- DIV3_WHEELS_ON: string (nullable = true)
#  |-- DIV3_TOTAL_GTIME: string (nullable = true)
#  |-- DIV3_LONGEST_GTIME: string (nullable = true)
#  |-- DIV3_WHEELS_OFF: string (nullable = true)
#  |-- DIV3_TAIL_NUM: string (nullable = true)
#  |-- DIV4_AIRPORT: string (nullable = true)
#  |-- DIV4_AIRPORT_ID: string (nullable = true)
#  |-- DIV4_AIRPORT_SEQ_ID: string (nullable = true)
#  |-- DIV4_WHEELS_ON: string (nullable = true)
#  |-- DIV4_TOTAL_GTIME: string (nullable = true)
#  |-- DIV4_LONGEST_GTIME: string (nullable = true)
#  |-- DIV4_WHEELS_OFF: string (nullable = true)
#  |-- DIV4_TAIL_NUM: string (nullable = true)
#  |-- DIV5_AIRPORT: string (nullable = true)
#  |-- DIV5_AIRPORT_ID: string (nullable = true)
#  |-- DIV5_AIRPORT_SEQ_ID: string (nullable = true)
#  |-- DIV5_WHEELS_ON: string (nullable = true)
#  |-- DIV5_TOTAL_GTIME: string (nullable = true)
#  |-- DIV5_LONGEST_GTIME: string (nullable = true)
#  |-- DIV5_WHEELS_OFF: string (nullable = true)
#  |-- DIV5_TAIL_NUM: string (nullable = true)
#  |-- YEAR: integer (nullable = true)


ORIGIN ORIGIN_WAC count_origin_wac avg_departure_delay avg_arrival_delay ATL 34 179264 8.49 2.40 ORD 41 142850 17.90 14.15 DFW 74 134432 11.89 10.14 DEN 82 102682 12.99 8.53 LAX 91 102232 9.49 6.98 IAH 74 79304 8.70 4.59 PHX 81 79128 8.33 5.66 SFO 91 75764 10.58 7.86 LAS 85 69142 10.22 6.09 MCO 33 61218 11.35 6.65 LGA 22 57204 17.41 13.14 DTW 43 57146 12.37 6.95 BOS 13 54376 12.80 10.86 MSP 63 54132 8.89 1.33 CLT 36 54048 7.48 4.43 EWR 21 52662 14.36 6.79 SLC 87 51950 4.84 -0.32 SEA 93 50834 6.78 2.03 JFK 22 50084 17.80 11.04 FLL 33 43354 11.52 4.56 BWI 35 41838 13.43 7.99 MDW 41 40468 12.50 4.55 DCA 38 39822 8.66 4.24 MIA 33 38950 11.74 6.41 TPA 33 36558 9.65 4.95 SAN 91 36310 7.50 3.78 PHL 23 33958 12.03 7.13 DAL 74 29970 9.53 4.29 HOU 74 27256 9.22 3.68 BNA 54 24458 9.28 4.33 STL 64 24296 8.77 3.01 HNL 2 22646 4.01 1.83 PDX 92 21464 4.94 0.46 OAK 91 21148 7.03 5.12 MSY 72 21010 7.14 1.57 RSW 33 20586 10.77 7.20 AUS 74 20364 9.50 4.19 IAD 38 19468 15.81 10.22 SJC 91 19340 6.15 4.68 MCI 64 19262 7.20 1.48 SNA 91 19000 5.90 2.45 SMF 91 18764 8.07 5.78 CLE 44 18000 10.45 6.31 RDU 36 16080 9.93 5.63 MKE 45 15750 10.05 3.57 SAT 74 15256 7.27 1.85 PBI 33 14692 14.17 11.43 SJU 3 13242 13.04 8.70 CMH 44 12788 12.56 7.09 IND 42 12760 8.87 3.07 PIT 23 12702 7.40 0.65 OGG 2 11228 5.16 1.69 CVG 52 10376 10.29 7.11 BUR 91 9982 6.20 3.16 BDL 11 9738 9.30 3.96 ABQ 86 9338 8.58 4.83 ONT 91 9118 8.05 5.15 OMA 65 9098 9.21 4.60 JAX 33 9078 8.37 5.00 TUS 81 8888 4.96 2.05 BUF 22 8184 10.40 4.88 OKC 73 8020 7.94 5.21 TUL 73 7870 6.15 3.07 RIC 38 7570 11.11 8.01 MEM 54 7420 9.97 6.75 PSP 91 6950 9.68 8.19 ANC 1 6844 2.56 -1.91 BHM 51 6812 9.27 5.06 RNO 85 6556 7.34 5.08 ELP 74 6302 7.45 4.80 GRR 43 6068 11.88 5.05 KOA 2 5874 4.06 1.34 PVD 15 5798 9.71 3.93 SDF 52 5720 9.81 4.58 LIH 2 5492 2.17 -0.21 BOI 83 5484 8.52 4.33 CHS 37 5476 6.89 3.04 LIT 71 5428 10.09 7.41 ORF 38 5040 12.30 8.41 GEG 93 5012 4.83 0.24 MSN 45 4952 7.78 5.62 MAF 74 4916 7.06 6.56 DSM 61 4838 14.18 10.56 XNA 71 4774 15.94 17.43 DAY 44 4710 8.21 5.03 LGB 91 4412 5.83 2.79 HPN 22 4186 16.77 15.34 GSO 36 4126 12.26 9.27 ICT 62 4106 10.87 8.26 ASE 82 4002 15.73 12.66 BTR 72 3958 10.14 10.86 FAT 91 3918 12.78 11.82 CID 61 3858 15.67 17.16 ROC 22 3766 11.48 7.00 SAV 34 3706 10.98 7.29 JAN 53 3700 8.94 7.98 PNS 33 3666 8.09 4.77 TYS 54 3636 14.23 13.04 ALB 22 3606 9.04 1.95 COS 82 3594 9.93 7.89 SGF 64 3572 13.35 14.32 CAK 44 3480 7.32 0.34 FSD 67 3336 11.30 10.58 GSP 37 3322 7.22 3.63 CRP 74 3302 8.12 7.83 SHV 72 3170 12.11 12.36 SBA 91 3086 9.36 7.43 CAE 37 3058 12.83 11.11 MHT 14 3004 10.19 2.77 ITO 2 3004 0.71 3.57 LEX 52 2964 9.71 5.57 AMA 74 2950 8.15 7.82 LFT 72 2908 7.96 9.10 FAR 66 2816 10.48 6.69 STT 4 2788 14.03 8.84 SYR 22 2770 10.90 8.57 MOB 51 2642 7.63 8.02 LBB 74 2624 7.84 8.15 GRB 45 2544 7.94 7.15 SBN 42 2492 16.30 13.48 SBP 91 2464 8.39 5.52 HSV 51 2438 6.35 4.01 FWA 42 2384 14.64 13.78 FNT 43 2374 4.73 -2.04 MLI 41 2342 12.72 12.24 VPS 33 2342 11.21 7.48 ISP 22 2324 12.33 4.66 GRK 74 2304 7.32 8.64 PIA 41 2268 13.28 11.64 SRQ 33 2206 14.05 9.08 MFE 74 2184 4.63 3.14 JAC 88 2098 10.22 3.00 GPT 53 2074 2.24 -0.82 CHA 54 2050 6.55 3.98 MYR 37 2024 9.10 10.50 ACY 21 2020 4.10 3.46 TLH 33 1964 7.67 3.73 MDT 23 1932 11.09 7.89 EUG 92 1890 7.18 2.93 EVV 42 1864 11.81 11.23 JNU 1 1772 6.48 5.98 BIS 66 1770 12.36 8.92 MRY 91 1742 8.81 7.37 ECP 33 1718 6.67 0.62 EGE 82 1702 14.89 9.82 AEX 72 1690 8.94 7.86 MGM 51 1678 7.89 8.46 HRL 74 1674 2.14 -1.19 BZN 84 1644 9.65 2.91 PWM 12 1608 10.29 4.20 GJT 82 1606 3.95 2.90 ISN 66 1530 9.03 5.02 BMI 41 1508 13.22 14.86 MLU 72 1502 8.88 8.80 ATW 45 1438 7.41 7.78 GNV 33 1412 11.10 9.79 ABI 74 1398 5.55 6.06 BFL 91 1358 7.20 5.06 BIL 84 1358 2.00 -4.04 TTN 21 1352 33.34 31.03 EYW 33 1346 2.04 -1.56 RAP 67 1324 4.98 1.78 BTV 16 1318 11.02 9.03 BRO 74 1296 6.63 6.57 TVC 43 1274 11.96 8.77 AVL 36 1248 9.64 6.04 LNK 65 1248 5.81 3.03 MFR 92 1246 8.91 6.89 AGS 34 1212 9.22 9.10 CLL 74 1202 7.66 8.77 CLD 91 1202 5.74 5.71 LRD 74 1202 3.

Output can only be rendered in Databricks

OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER count_carrier avg_departure_delay avg_arrival_delay WN 19393 WN 598918 9.84 3.38 DL 19790 DL 398942 8.76 1.81 EV 20366 EV 298506 9.88 8.43 OO 20304 OO 284362 9.54 7.74 AA 19805 AA 259720 10.67 7.03 UA 19977 UA 236466 14.27 6.09 US 20355 US 196316 6.65 4.39 MQ 20398 MQ 169972 15.56 16.68 B6 20409 B6 127928 14.81 11.99 AS 19930 AS 79454 2.99 -0.54 NK 20416 NK 52464 14.11 12.45 F9 20436 F9 39176 20.99 21.64 HA 19690 HA 37064 1.54 4.28 VX 21171 VX 27654 9.93 4.73

Output can only be rendered in Databricks

tail_num flight_status count_flights avg_departure_delay avg_arrival_delay null Cancelled 0 null null D942DN null 12 -2.00 -8.50 D942DN Delayed 6 23.33 16.00 N001AA null 284 -2.99 -4.49 N001AA Cancelled 2 null null N001AA Delayed 60 52.83 54.40 N002AA null 308 -2.28 -3.26 N002AA Cancelled 2 null null N002AA Delayed 56 45.07 39.64 N003AA null 290 -2.66 -5.01 N003AA Cancelled 6 null null N003AA Delayed 90 83.07 81.18 N004AA null 308 -3.34 -5.58 N004AA Delayed 62 41.26 35.77 N005AA null 320 -2.51 -4.42 N005AA Cancelled 14 null null N005AA Delayed 58 87.72 89.21 N006AA null 332 -3.35 -4.38 N006AA Cancelled 6 null null N006AA Delayed 44 56.32 49.45 N007AA null 282 -2.50 -3.77 N007AA Cancelled 22 180.00 null N007AA Delayed 70 89.91 85.41 N008AA null 188 -2.97 -5.60 N008AA Cancelled 10 null null N008AA Delayed 48 85.25 83.75 N009AA null 298 -2.89 -5.26 N009AA Cancelled 4 null null N009AA Delayed 64 63.81 61.16 N010AA null 252 -2.51 -4.09 N010AA Cancelled 10 null null N010AA Delayed 56 63.50 65.25 N011AA null 314 -2.59 -5.11 N011AA Cancelled 12 null null N011AA Delayed 62 49.90 51.65 N012AA null 292 -2.87 -6.01 N012AA Cancelled 20 null null N012AA Delayed 64 42.63 43.10 N013AA null 262 -2.24 -4.61 N013AA Cancelled 6 62.00 null N013AA Delayed 62 52.97 50.06 N014AA null 236 -2.27 -3.85 N014AA Cancelled 10 null null N014AA Delayed 88 61.34 62.20 N015AA null 260 -3.02 -5.52 N015AA Cancelled 6 null null N015AA Delayed 64 52.38 48.06 N016AA null 348 -3.60 -6.28 N016AA Cancelled 14 null null N016AA Delayed 54 31.00 28.52 N017AA null 276 -2.64 -3.14 N017AA Cancelled 8 null null N017AA Delayed 64 56.56 53.63 N018AA null 320 -2.98 -5.76 N018AA Cancelled 12 null null N018AA Delayed 58 44.03 42.32 N019AA null 310 -3.28 -5.50 N019AA Cancelled 16 null null N019AA Delayed 38 59.00 58.68 N020AA null 318 -3.42 -3.89 N020AA Cancelled 4 null null N020AA Delayed 64 65.50 61.22 N021AA null 284 -3.42 -5.80 N021AA Cancelled 8 null null N021AA Delayed 66 47.70 44.03 N022AA null 374 -2.71 -5.21 N022AA Cancelled 10 null null N022AA Delayed 42 34.62 31.43 N023AA null 224 -2.51 -5.54 N023AA Cancelled 18 35.00 null N023AA Delayed 54 63.74 63.70 N024AA null 296 -3.90 -5.80 N024AA Cancelled 4 null null N024AA Delayed 74 50.27 49.36 N025AA null 298 -3.71 -5.03 N025AA Cancelled 2 null null N025AA Delayed 82 78.39 76.28 N026AA null 200 -2.33 -3.87 N026AA Cancelled 8 -4.00 null N026AA Delayed 32 47.94 46.06 N027AA null 228 -2.12 -4.89 N027AA Cancelled 6 null null N027AA Delayed 38 85.32 84.53 N028AA null 132 -3.24 -5.12 N028AA Cancelled 6 null null N028AA Delayed 18 216.89 210.00 N029AA null 56 -2.82 -4.64 N029AA Delayed 22 76.36 66.00 N0EGMQ null 496 -3.05 -3.47 N0EGMQ Cancelled 82 26.00 null N0EGMQ Delayed 234 66.28 72.38 N10156 null 140 -2.54 -2.83 N10156 Delayed 42 43.33 45.52 N102UW null 564 -2.00 -4.78 N102UW Delayed 126 50.86 45.16 N103SY null 344 -0.46 -0.87 N103SY Cancelled 26 null null N103SY Delayed 158 56.10 49.17 N103US null 554 -2.08 -4.63 N103US Delayed 126 67.78 62.21 N104UW null 538 -1.48 -3.71 N104UW Delayed 120 47.65 40.85 N10575 null 736 -3.30 -3.24 N10575 Cancelled 48 null null N10575 Delayed 146 57.38 60.38 N105SY null 404 -0.69 -1.65 N105SY Cancelled 18 null null N105SY Delayed 154 94.42 93.30 N105UW null 480 -1.27 -2.46 N105UW Delayed 116 60.10 58.54 N106SY null 306 0.01 -1.63 N106SY Cancelled 34 9.00 null N106SY Delayed 206 61.00 58.18 N107SY null 380 -0.39 -1.12 N107SY Cancelled 24 53.00 null N107SY Delayed 182 61.51 58.93 N107US null 550 -1.93 -3.67 N107US Cancelled 2 20.00 null N107US Delayed 88 53.41 55.70 N108SY null 410 -1.02 -3.33 N108SY Cancelled 4 null null N108SY Delayed 182 80.12 77.22 N108UW null 528 -1.53 -3.40 N108UW Delayed 108 67.74 59.04 N109SY null 410 -0.27 -1.27 N109SY Cancelled 18 null null N109SY Delayed 170 64.01 64.82 N109UW null 514 -1.54 -4.53 N109UW Delayed 146 53.51 47.93 N110SY null 392 -0.71 -2.07 N110SY Cancelled 28 null null N110SY Delayed 208 72.35 71.41 N110UW null 424 -2.10 -5.80 N110UW Delayed 60 32.83 29.30 

---------------------------------------------------------------------------
TypeError Traceback (most recent call last)
 in ()
----> 1 df_origin['avg_arrival_delay'].sum()
 2 
 3 fig, ax = plt.subplots()
 4 rects1 = ax.bar( df_origin['avg_arrival_delay'])
 5 rects2 = ax.bar(df_origin['avg_departure_delay'])

TypeError: 'Column' object is not callable

In [0]:
df_weatherRAW.createOrReplaceTempView('weather')

# Number of flights by origin airport
df_weather = sqlContext.sql("""
WITH cte as (select 
             a.name,
             a.longitude,
             a.latitude,
             a.station,
             a.year, 
             count(a.name) as count_records
             
             from weather as a
             where (latitude > 24.5 and latitude < 49.5) and (longitude < -66.5 and longitude > -125)
             group by 1, 2, 3, 4, 5
             order by 1)
 
select 
*
from cte  
""")


display(df_weather)


# |-- STATION: string (nullable = true)
#  |-- DATE: string (nullable = true)
#  |-- LATITUDE: string (nullable = true)
#  |-- LONGITUDE: string (nullable = true)
#  |-- ELEVATION: string (nullable = true)
#  |-- NAME: string (nullable = true)
#  |-- REPORT_TYPE: string (nullable = true)
#  |-- SOURCE: string (nullable = true)
#  |-- HourlyAltimeterSetting: string (nullable = true)
#  |-- HourlyDewPointTemperature: string (nullable = true)
#  |-- HourlyDryBulbTemperature: string (nullable = true)
#  |-- HourlyPrecipitation: string (nullable = true)
#  |-- HourlyPresentWeatherType: string (nullable = true)
#  |-- HourlyPressureChange: string (nullable = true)
#  |-- HourlyPressureTendency: string (nullable = true)
#  |-- HourlyRelativeHumidity: string (nullable = true)
#  |-- HourlySkyConditions: string (nullable = true)
#  |-- HourlySeaLevelPressure: string (nullable = true)
#  |-- HourlyStationPressure: string (nullable = true)
#  |-- HourlyVisibility: string (nullable = true)
#  |-- HourlyWetBulbTemperature: string (nullable = true)
#  |-- HourlyWindDirection: string (nullable = true)
#  |-- HourlyWindGustSpeed: string (nullable = true)
#  |-- HourlyWindSpeed: string (nullable = true)
#  |-- Sunrise: string (nullable = true)
#  |-- Sunset: string (nullable = true)
#  |-- DailyAverageDewPointTemperature: string (nullable = true)
#  |-- DailyAverageDryBulbTemperature: string (nullable = true)
#  |-- DailyAverageRelativeHumidity: string (nullable = true)
#  |-- DailyAverageSeaLevelPressure: string (nullable = true)
#  |-- DailyAverageStationPressure: string (nullable = true)
#  |-- DailyAverageWetBulbTemperature: string (nullable = true)
#  |-- DailyAverageWindSpeed: string (nullable = true)
#  |-- DailyCoolingDegreeDays: string (nullable = true)
#  |-- DailyDepartureFromNormalAverageTemperature: string (nullable = true)
#  |-- DailyHeatingDegreeDays: string (nullable = true)
#  |-- DailyMaximumDryBulbTemperature: string (nullable = true)
#  |-- DailyMinimumDryBulbTemperature: string (nullable = true)
#  |-- DailyPeakWindDirection: string (nullable = true)
#  |-- DailyPeakWindSpeed: string (nullable = true)
#  |-- DailyPrecipitation: string (nullable = true)
#  |-- DailySnowDepth: string (nullable = true)
#  |-- DailySnowfall: string (nullable = true)
#  |-- DailySustainedWindDirection: string (nullable = true)
#  |-- DailySustainedWindSpeed: string (nullable = true)
#  |-- DailyWeather: string (nullable = true)
#  |-- MonthlyAverageRH: string (nullable = true)
#  |-- MonthlyDaysWithGT001Precip: string (nullable = true)
#  |-- MonthlyDaysWithGT010Precip: string (nullable = true)
#  |-- MonthlyDaysWithGT32Temp: string (nullable = true)
#  |-- MonthlyDaysWithGT90Temp: string (nullable = true)
#  |-- MonthlyDaysWithLT0Temp: string (nullable = true)
#  |-- MonthlyDaysWithLT32Temp: string (nullable = true)
#  |-- MonthlyDepartureFromNormalAverageTemperature: string (nullable = true)
#  |-- MonthlyDepartureFromNormalCoolingDegreeDays: string (nullable = true)
#  |-- MonthlyDepartureFromNormalHeatingDegreeDays: string (nullable = true)
#  |-- MonthlyDepartureFromNormalMaximumTemperature: string (nullable = true)
#  |-- MonthlyDepartureFromNormalMinimumTemperature: string (nullable = true)
#  |-- MonthlyDepartureFromNormalPrecipitation: string (nullable = true)
#  |-- MonthlyDewpointTemperature: string (nullable = true)
#  |-- MonthlyGreatestPrecip: string (nullable = true)
#  |-- MonthlyGreatestPrecipDate: string (nullable = true)
#  |-- MonthlyGreatestSnowDepth: string (nullable = true)
#  |-- MonthlyGreatestSnowDepthDate: string (nullable = true)
#  |-- MonthlyGreatestSnowfall: string (nullable = true)
#  |-- MonthlyGreatestSnowfallDate: string (nullable = true)
#  |-- MonthlyMaxSeaLevelPressureValue: string (nullable = true)
#  |-- MonthlyMaxSeaLevelPressureValueDate: string (nullable = true)
#  |-- MonthlyMaxSeaLevelPressureValueTime: string (nullable = true)
#  |-- MonthlyMaximumTemperature: string (nullable = true)
#  |-- MonthlyMeanTemperature: string (nullable = true)
#  |-- MonthlyMinSeaLevelPressureValue: string (nullable = true)
#  |-- MonthlyMinSeaLevelPressureValueDate: string (nullable = true)
#  |-- MonthlyMinSeaLevelPressureValueTime: string (nullable = true)
#  |-- MonthlyMinimumTemperature: string (nullable = true)
#  |-- MonthlySeaLevelPressure: string (nullable = true)
#  |-- MonthlyStationPressure: string (nullable = true)
#  |-- MonthlyTotalLiquidPrecipitation: string (nullable = true)
#  |-- MonthlyTotalSnowfall: string (nullable = true)
#  |-- MonthlyWetBulb: string (nullable = true)
#  |-- AWND: string (nullable = true)
#  |-- CDSD: string (nullable = true)
#  |-- CLDD: string (nullable = true)
#  |-- DSNW: string (nullable = true)
#  |-- HDSD: string (nullable = true)
#  |-- HTDD: string (nullable = true)
#  |-- NormalsCoolingDegreeDay: string (nullable = true)
#  |-- NormalsHeatingDegreeDay: string (nullable = true)
#  |-- ShortDurationEndDate005: string (nullable = true)
#  |-- ShortDurationEndDate010: string (nullable = true)
#  |-- ShortDurationEndDate015: string (nullable = true)
#  |-- ShortDurationEndDate020: string (nullable = true)
#  |-- ShortDurationEndDate030: string (nullable = true)
#  |-- ShortDurationEndDate045: string (nullable = true)
#  |-- ShortDurationEndDate060: string (nullable = true)
#  |-- ShortDurationEndDate080: string (nullable = true)
#  |-- ShortDurationEndDate100: string (nullable = true)
#  |-- ShortDurationEndDate120: string (nullable = true)
#  |-- ShortDurationEndDate150: string (nullable = true)
#  |-- ShortDurationEndDate180: string (nullable = true)
#  |-- ShortDurationPrecipitationValue005: string (nullable = true)
#  |-- ShortDurationPrecipitationValue010: string (nullable = true)
#  |-- ShortDurationPrecipitationValue015: string (nullable = true)
#  |-- ShortDurationPrecipitationValue020: string (nullable = true)
#  |-- ShortDurationPrecipitationValue030: string (nullable = true)
#  |-- ShortDurationPrecipitationValue045: string (nullable = true)
#  |-- ShortDurationPrecipitationValue060: string (nullable = true)
#  |-- ShortDurationPrecipitationValue080: string (nullable = true)
#  |-- ShortDurationPrecipitationValue100: string (nullable = true)
#  |-- ShortDurationPrecipitationValue120: string (nullable = true)
#  |-- ShortDurationPrecipitationValue150: string (nullable = true)
#  |-- ShortDurationPrecipitationValue180: string (nullable = true)
#  |-- REM: string (nullable = true)
#  |-- BackupDirection: string (nullable = true)
#  |-- BackupDistance: string (nullable = true)
#  |-- BackupDistanceUnit: string (nullable = true)
#  |-- BackupElements: string (nullable = true)
#  |-- BackupElevation: string (nullable = true)
#  |-- BackupEquipment: string (nullable = true)
#  |-- BackupLatitude: string (nullable = true)
#  |-- BackupLongitude: string (nullable = true)
#  |-- BackupName: string (nullable = true)
#  |-- WindEquipmentChangeDate: string (nullable = true)
#  |-- YEAR: integer (nullable = true)

name longitude latitude station year count_records 068 BAFFIN BAY POINT OF ROCKS TX, TX US -97.42 27.3 99471099999 2015 2123 9014098 FORT GRATIOT MI, US -82.42 43.01 99725899999 2015 2122 9052030 OSWEGO NY, US -76.51 43.46 99726499999 2015 2122 9063020 BUFFALO NY, US -78.89 42.88 99725499999 2015 2122 9075014 HARBOR BEACH MI, US -82.64 43.85 99726099999 2015 2123 9075099 DE TOUR VILLAGE MI, US -83.9 45.99 99725799999 2015 2122 9076024 ROCK CUT MI, US -84.19 46.27 99726699999 2015 2124 9076070 S.W. PIER MI, US -84.37 46.5 99726899999 2015 2124 9087023 LUDINGTON MI, US -86.44 43.95 99726199999 2015 2124 9087044 CALUMET IL, US -87.54 41.73 99725599999 2015 2112 9099004 POINT IROQUOIS MI, US -84.63 46.49 99726599999 2015 2032 9099018 MARQUETTE C.G. MI, US -87.38 46.55 99726299999 2015 2122 9099090 GRAND MARAIS MN, US -90.34 47.75 99725999999 2015 2120 ABBEVILLE CHRIS CRUSTA MEMORIAL AIRPORT, LA US -92.084 29.976 72058700184 2015 5244 ABBOTSFORD, CA -122.363333 49.025278 71108099999 2015 2875 ABERDEEN 35 WNW, SD US -99.12958 45.71145 99999954933 2015 26013 ABERDEEN PHILLIPS FIELD, MD US -76.1697 39.4716 72405713701 2015 919 ABERDEEN REGIONAL AIRPORT, SD US -98.413 45.4433 72659014929 2015 3337 ABILENE DYESS AFB, TX US -99.85 32.43333 72096513910 2015 3357 ABILENE REGIONAL AIRPORT, TX US -99.6822 32.4105 72266013962 2015 3236 ABINGDON VIRGINIA HIGHLANDS AIRPORT, VA US -82.03333 36.68333 72405853818 2015 6525 ABRAHAM GONZALEZ INTERNATIONAL, MX -106.428667 31.636133 76075399999 2015 1436 ACE BASIN RESERVE, SC US -80.45 32.55 99799099999 2015 1422 ADA MUNICIPAL AIRPORT, OK US -96.67111 34.80417 72204453930 2015 6471 ADRIAN LENAWEE CO AIRPORT, MI US -84.07944 41.86778 72540404847 2015 3133 AEROFLEX ANDOVER AIRPORT, NJ US -74.73633 41.00928 72407754779 2015 2247 AFTON MUNICIPAL, WY US -110.942164 42.711247 72051699999 2015 6470 AGASSIZ CS, CA -121.7666666 49.25 71113099999 2015 2752 AHOSKIE TRI CO AIRPORT, NC US -77.17083 36.2975 72307993796 2015 6523 AIKEN MUNICIPAL AIRPORT, SC US -81.683 33.65 72060100193 2015 6495 AINSWORTH MUNICIPAL AIRPORT, NE US -100.00056 42.57694 72555694975 2015 6495 AITKIN MUNICIPAL AIRPORT, MN US -93.67667 46.5475 72750494999 2015 6428 AKRON CANTON AIRPORT, OH US -81.4435 40.9181 72521014895 2015 3228 AKRON FULTON INTERNATIONAL AIRPORT, OH US -81.46417 41.0375 72430314813 2015 3668 AKRON WASHINGTON CO AIRPORT, CO US -103.21667 40.16667 72469824015 2015 2998 ALABASTER SHELBY CO AIRPORT, AL US -86.78167 33.17833 72230053864 2015 3169 ALAMEDA, CA US -122.298 37.772 99403399999 2015 2124 ALAMINOS CANYON, TX US -94.68333 26.93333 72095400456 2015 6221 ALAMOGORDO WHITE SANDS REGIONAL AIRPORT, NM US -105.99056 32.83972 72269393097 2015 6520 ALAMOSA BERGMAN FIELD, CO US -105.8613 37.4389 72462023061 2015 3446 ALBANY INTERNATIONAL AIRPORT, NY US -73.79912 42.74722 72518014735 2015 3564 ALBANY SW GEORGIA REGIONAL AIRPORT, GA US -84.19444 31.53556 72216013869 2015 3080 ALBERT LEA MUNICIPAL AIRPORT, MN US -93.36667 43.68333 72658994968 2015 6542 ALBERTVILLE MUNICIPAL AIRPORT, AL US -86.25583 34.22917 72037663880 2015 6519 ALBION MUNICIPAL AIRPORT, NE US -98.05444 41.73 72344154921 2015 6502 ALBUQUERQUE DOUBLE EAGLE II AIRPORT, NM US -106.795 35.145 72364703034 2015 3626 ALBUQUERQUE INTERNATIONAL AIRPORT, NM US -106.6155 35.0419 72365023050 2015 3179 ALEXANDER CITY THOMAS C RUSSELL FIELD AIRPORT, AL US -85.96278 32.91472 72026563833 2015 6524 ALEXANDRIA BAY, NY US -75.9333333 44.3333333 99822399999 2015 2122 ALEXANDRIA CHANDLER FIELD, MN US -95.3941 45.8679 72655714910 2015 3095 ALEXANDRIA ESLER FIELD, LA US -92.2907 31.3953 72248713935 2015 2997 ALEXANDRIA INTERNATIONAL AIRPORT, LA US -92.55861 31.33472 74754093915 2015 3213 ALGOMA CITY MARINA, WI US -87.43 44.6 99497299999 2015 279 ALGONA MUNICIPAL AIRPORT, IA US -94.27194 43.07778 72545704904 2015 6526 ALGONAC, MI US -82.527 42.621 99849299999 2015 2105 ALGONQUIN PARK EAST GATE, CA -78.2666666 45.5333333 71581099999 2015 4633 ALICE INTERNATIONAL AIRPORT, TX US -98.02472

In [0]:
df_airports.createOrReplaceTempView('airports')

# Number of flights by origin airport
df_airport_summary = sqlContext.sql("""
WITH cte as (select 
             a.iso_region,
             count(a.iso_region) as count_airports_by_state
             
             from airports as a
             where a.iso_country = 'US'
             group by 1
             order by 2 desc
             )
 
select 
*
from cte  
""")


display(df_airport_summary)

iso_region count_airports_by_state US-TX 3589 US-CA 2303 US-FL 1204 US-AK 1034 US-IL 1026 US-PA 990 US-AZ 958 US-OH 896 US-LA 804 US-NY 759 US-IN 749 US-MO 694 US-WA 692 US-OK 667 US-WI 652 US-MI 636 US-MN 627 US-CO 601 US-GA 600 US-OR 597 US-NC 560 US-VA 555 US-KS 506 US-AR 493 US-NJ 461 US-AL 453 US-ID 428 US-NM 422 US-UT 406 US-TN 403 US-MT 399 US-IA 394 US-NV 366 US-MS 334 US-ND 334 US-NE 334 US-KY 310 US-MD 287 US-MA 272 US-SC 258 US-ME 251 US-SD 229 US-NH 200 US-WY 196 US-CT 168 US-WV 148 US-HI 120 US-VT 115 US-DE 60 US-RI 40 US-DC 20

Output can only be rendered in Databricks

In [0]:
### Plots
# df_origin = df_origin.toPandas().convert_dtypes()
# df_origin.select('avg_departure_delay').sort_index().plot.bar()
# plt.title('Delays Outcome Distribution (15+ min late)')

# plt.hist(df_origin['avg_departure_delay'])
# plt.show()

# plt.hist(df['release_year'])
# plt.show()

In [0]:
print(df_airport_summary.columns)
print(type(df_airport_summary))

['iso_region', 'count_airports_by_state']
<class 'pyspark.sql.dataframe.DataFrame'>


In [0]:
df_airport_summary.withColumn('iso_region', regexp_replace('iso_region', 'US-', '')).show(truncate=False)

+----------+-----------------------+
|iso_region|count_airports_by_state|
+----------+-----------------------+
|TX        |3589                   |
|CA        |2303                   |
|FL        |1204                   |
|AK        |1034                   |
|IL        |1026                   |
|PA        |990                    |
|AZ        |958                    |
|OH        |896                    |
|LA        |804                    |
|NY        |759                    |
|IN        |749                    |
|MO        |694                    |
|WA        |692                    |
|OK        |667                    |
|WI        |652                    |
|MI        |636                    |
|MN        |627                    |
|CO        |601                    |
|GA        |600                    |
|OR        |597                    |
+----------+-----------------------+
only showing top 20 rows



In [0]:
# fig = px.choropleth(df_airport_summary,locations='iso_region',locationmode="USA-states",scope="usa",color='Flights by State',color_continuous_scale="Viridis_r")
# fig.show()

---------------------------------------------------------------------------
ValueError                                Traceback (most recent call last)
<command-4295587629775004> in <cell line: 1>()
----> 1 fig = px.choropleth(df_airport_summary,locations='iso_region',locationmode="USA-states",scope="usa",color='Flights by State',color_continuous_scale="Viridis_r")
      2 fig.show()

/databricks/python/lib/python3.9/site-packages/plotly/express/_chart_types.py in choropleth(data_frame, lat, lon, locations, locationmode, geojson, featureidkey, color, facet_row, facet_col, facet_col_wrap, facet_row_spacing, facet_col_spacing, hover_name, hover_data, custom_data, animation_frame, animation_group, category_orders, labels, color_discrete_sequence, color_discrete_map, color_continuous_scale, range_color, color_continuous_midpoint, projection, scope, center, fitbounds, basemap_visible, title, template, width, height)
   1089     colored region mark on a map.
   1090     """
-> 1091     retur

In [0]:
# vector_col = "corr_features"
# assembler = VectorAssembler(inputCols=['col1','col2','col3'], 
#                             outputCol=vector_col)
# myGraph_vector = assembler.transform(myGraph).select(vector_col)
# matrix = Correlation.corr(myGraph_vector, vector_col)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
<command-917638415058434> in <cell line: 4>()
      2 assembler = VectorAssembler(inputCols=['col1','col2','col3'], 
      3                             outputCol=vector_col)
----> 4 myGraph_vector = assembler.transform(myGraph).select(vector_col)
      5 matrix = Correlation.corr(myGraph_vector, vector_col)

NameError: name 'myGraph' is not defined

### II. EDA Findings


We completed an initial EDA to get a better understanding of the data to help inform the next steps of the project, starting with the airline dataset. It appears that some airports are more prone to delays than others. For example, Orlando is the second busiest airport in the country based on the 3 month sample and it had an average departure delay of ~18 minutes. This is significantly more than the busiest airport in the country, Atlanta, with an average delay of ~8 minutes. A few others that stand out include Dallas Forth-Worth and Denver with an average delay of ~12 minutes and ~13 minutes, respectively. This helps us inform the idea that a busy airport can result in more and longer delays, however, this is not always the case (such as with Atlanta and Los Angeles). There are several other variables to review to better understand the circumstances of delays. 

We reviewed delays by carrier and there are noticable differences between airlines. For example, Southwest (WN) and Delta (DL) have average delays of ~9 minutes as compared to United with an average delay of ~14 minutes.  

Additionally, we did a brief EDA on planes (by tail number) to inform the hypothesis that certain planes can cause delays and cancellations. From a brief review, it appears as though certain planes are more likely to be delayed or cancelled, however, this is at best speculation because we do not have maintenance data, so it could be a result of certain planes flying routes that are more prone to delays (e.g., far North routes in the winter). We will attempt to explore this topic further.

Lastly, we briefly looked into the weather dataset and initial findings is that a majority of the variables are null, and specific columns will be useful (e.g., hourly precipitation, hourly sky conditions, hourly visibility).

### III.  Question Formulation
Can we accurately predict a flight delay? Flight delays are a significant inconveience to passengers, airlines, airline staff, and airport staff. We will be analyzing the airlines dataset, weather dataset, and stations data and applying machine learning models and statistical concepts to determine if we can accurately predict delays as defined as 15 minutes or more. The goal would be to identify these key factors to educate airlines and airports to avoid future delays when possible. 

The initial question can be thought of as a classification model, e.g., is the flight cancelled or not? This can be further explored with a regression model where, if a flight is delayed, can we predict how long the delay is?

**Audience**

Given the initial findings in the EDA, we will focus this project with United Airlines as the audience in mind. We will review the data to help us better understand the factors that drive United's higher average delays to allow them to get ahead of the issue and provide a better client experience. Given that they are the sixth largest carrier within this sample dataset, size is likely not a leading factor to longer delays given that the top five largest have significantly lower average delay times. There could be specific factors that are potentially within United's control that leads to longer delay times and we would like to be able to inform. 

With the audience in mind, we will be analyzing the data with the key question in mind of "can we accurately predict a flight  delay?" This will potentially branch out into additional questions such as (1) which factors result in delays, (2) which of these factors are within United's control that they can get ahead of, (3) which of these factors are not within their control but can work with associated/involved parties to potentially limit impact.

## IV. Project Plan

### I. Algorithms in Consideration
We will use the following algorithms for our analysis:


#### Classification Algorithms

**Logistic Regression:** Logistic regression is a classification learning algorithm that uses the standard logistic function to predict outcomes. In the case of airlines delays, we are looking to do multiclass classification to determine whether a flight is likely to be on time, ddelayed, or canceled. A logistic regression multiclass classification will serve as our baseline model. 

#### Regression Algorithms

**Linear Regression:** Linear regression is a relatively simple algorithm, which often ends up performing very well. We will start our exploration of delay prediction with linear regression to get a baseline. 

#### Classification & Regression Algorithms

All of the following models can be used for both classification and regression, and we will attempt to utilize them for both tasks. 

**Decision Trees:** Decision trees are a machine learning algorithm that recursively splits the data into root nodes and child nodes based on the training examples. It is a recursive exercise and the splitting of the data is dependent on new error rates for the model. We can either leverage classification trees (on-time, delay, or cancellation) or regression trees (predicted length of delay).

**XGBoost:** XGBoost is a highly efficient and optimized distributed gradient boosting library, which implements machine learning algorithms under the Gradient Boosting framework. XGBoost provides tree boosting to solve data science problems quickly and effectively. XGBoost builds trees in series, with each building on the previous one. 

**Random Forest:** Random forests are an ensemble algorithm that build on decision trees. Random forests learn in parallel, and then take the average from all the trees built.

### II. Measuring Model Success

We will analyze our models in terms of statistical concepts that measure model success. These concepts include (where applicable, depending on the model):

#### Classification Metrics

**Precision:** Defined as proportion of correctly predicted positives of total predicted positives, can also be referred to as positive predictive value. 

$$ Precision = \frac{TP}{TP+FP} $$

**Recall:** Defined as proportion of correctly identified positives, can also be referred to as the true positive rate or sensitivity.

$$ Recall = \frac{TP}{TP+FN} $$

**F-score:** Measure of a model's accuracy. It is calculated from the precision and recall of the model, where the precision is the number of true positive results divided by the number of all positive results

$$ F1 = \frac{2 * Precision * Recall}{Precision + Recall} = \frac{2 * TP}{2 * TP + FP + FN} $$

**Accuracy:** All true prediction over all predictions.

$$ Accuracy = \frac{TP+TN}{TP+TN+FP+FN}  $$

#### Regression Metrics 

**Mean Squared Error:** Defined as the average squared difference between the estimated values and the actual value. MSE is always strictly positive by the nature of the calculation. The MSE is a measure of the quality of an estimator, derived from the square of Euclidean distance.

$$ \sum_{i=1}^{D}(x_i-y_i)^2 $$

**R-Squared:** R-squared is a statistical measure that represents the proportion of the variance for a dependent variable that's explained by an independent variable or variables in a regression model.

$$ R^2 = 1 - \frac{RSS}{TSS} $$

**Adjusted R-Squared:** Adjusted R-squared is similar in nature to R-Squared but it is weighted against the number of independent variable used. 

$$ R^2 = 1 - \frac{SS_{res} / (n - K)}{SS_{tot} / (n - 1)} $$

## V. Data Pipeline

### I. Pipeline Explanation

![Pipeline](https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/Algorithm_flowchart_example__1_.jpeg)

**Explanation:**
 - We will load the data from CSV files (some provided by the instructors and some third-party datasets). We will extract the data into Databricks and do our data preparation from there. 
 - Data preparation starts with data processing & wrangling, in which we collect all the data do some basic EDA. Once we have thoroughly completed the exploratory data analysis, we will do feature engineering on the data. We will complete any joins necessary and split our data into train/validate/test sets. Then we will choose the features to inclued in model and do any standardization or normalization needed. 
 - Then we will enter the iterative process of modeling. We train various models on our training data and based on the evaluation metrics we will tune our model and go back to data preparation to make improvements. 
 - Lastly, we will deploy the model to production and continuously monitor the model.

### II. Joining

- Weather and stations datasets can be joined on station_id.
- To join the airlines dataset with weather/stations we need to be able to find the latitude and longitude of each airport and join the airports to the nearest weather station. That is why will need to bring in the third-party dataset of airport data, so that we can find the location of the airports.

### II. Split Dataset

We will split the data into a train, validation, and test set. Given the large amount of data that we have, we have plenty of data to create three splits. This will also allow us to train various models and iterate on our model training. We will also like to do cross-validation on our data. Given that it is time series data, we will need to do cross validation on a rolling basis. We will take subsets of data, and predict the future data and compare of forecases against the actual data. Those same forecasted data points are included in the next training dataset and a forecast is made on that data.

## VI. Project Team

### I. Team Members

Briana Hart \
briana.hart@berkeley.edu

<img src="https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/_DSC9588.jpg" alt="test" width="200"/>

Oleg Ananyev \
olegananyev@berkeley.edu

<img src="https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/20220808_MiMsPortraits_bhs_025 2.jpeg" alt="test" width="200"/>

Annie Passan \
anuradha.passan@berkeley.edu

<img src="https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/_DSC9588.jpg" alt="test" width="200"/>

Neil Prabhu \
neilprabhu@berkeley.edu

<img src="https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/Screen Shot 2022-10-30 at 6.32.49 PM.jpg" alt="test" width="200"/>

### II. Phase Leader Plan


| Task       | Leader |
|------------|--------|
| Phase I    | Neil   |
| Phase II   | Oleg   |
| Phase III  | Annie  |
| Phase IV   | Bri    |
| Phase V    | Neil    |

### III. Credit Assignment

| Task                           | Contributors       |
|--------------------------------|-------------|
| Databricks Setup               | Neil, Bri   |
| Notebook Setup                 | Oleg, Annie |
| Explain Data                   | Oleg, Annie |
| Define The Outcome             | Everyone        |
| Ingest CSV Files Efficiently   | Bri         |
| Describe Table Join Plan       | Annie       |
| Checkpoint to Blob Storage     | Neil        |
| Select ML models   | Bri         |
| Split Validation and Test Data | Neil        |
| Update project leaderboad      | Neil        |

### IV. Phase 2 Planning

![Gantt](https://raw.githubusercontent.com/brianahart/spark_flight_predictions/main/gantt.png)

[Monday.com project plan](https://berkeley417683.monday.com/boards/3393322628/views/78370466)

The current plan for executing phase 2 is outlined in the table below:

| Task                                                                             | Contributor(S) |
|----------------------------------------------------------------------------------|----------------|
| EDA on all tables                                                                | Annie          |
| List out raw features, derived features that will be used                        | Annie |
| Join tables (full join of all the data) to generate final dataset                | Neil|
| Store final dataset on cold blob storage on overwrite mode                       | Neil|
| EDA on joined dataset that will be used for training and evaluation              | Bri|
| Address missing data                                                             | Oleg|
| Address non-numerical features                                                   | Oleg|
| Address (maybe implement) dimensionality reduction                               | Bri|
| Create any derived features                                                      | Annie|
| Address feature transformations for pipeline                                     | Bri|
| Other feature engineering efforts                                                | Oleg|
| Create baseline pipelines and do experiments on ALL the data                     | Neil|
| Update the Project Leaderboard  with best pipeline details and results      | Neil|

## VII. Next Steps, Conclusion, Open Issues

**Next Steps:**
We will continue with EDA on the four key tables identified to determine the most appropirate way to clean the data, split the data, and join the tables together. We will add the final table to the blob storage to test our models against. We will train the model for optimal performance with a focus on balance against overengineering and accuracy. We will then scale the model against the full dataset.    


**Conclusion:**
We will develop a model which will answer the key question on whether we can accurately predict a flight delay. It would start with a classification model to determine if we can predict a flight cancelation. Furthermore, for those non-cancelled flights, we will use regression algorithms to predict the length of the potential delay. We will use our findings to advise our client, United Airlines, to provide them an opportunity to improve their operations and the client experience. 

**Open Issues:**
Key issues we will consider in future phases is how to appropropriately cleanse the data for missing values and transform any existing variables. Furthermore, we will need to join the weather and airline data with caution considering the following factors: (1) matching time zones for weather data and airline data, (2) matching locations across weather stations and airline/airport data.